In [1]:
import sys
sys.path.insert(0, '../')
from gw_tools.gw_plot import gw_plot
from gw_tools import data_prep
from gw_tools.gw_LSTM import gw_LSTM
import datetime
import IPython
import IPython.display
import numpy as np
import pandas as pd
import pickle
from sklearn.model_selection import TimeSeriesSplit
from sklearn.model_selection import GridSearchCV
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
import time

In [2]:
df = data_prep.select_features(pd.read_pickle('../data/pickled_data/APK309_short.pkl'))
df = data_prep.add_toy_signal(df).set_index('date')

TEST_SIZE = 365 # size of the test set 

X_train = df[:-TEST_SIZE].copy()
X_test = df[-TEST_SIZE:].copy()

y_train = X_train.avg_well_depth.copy().values
y_test = X_test.avg_well_depth.copy().values

well_tr_mean = np.mean(X_train.avg_well_depth.values)
well_tr_std = np.std(X_train.avg_well_depth.values)

In [3]:
## Prepare the pipeline
scaler =  StandardScaler(copy=True)
gw_LSTM = gw_LSTM()

pipe = Pipeline([('scaler', scaler), 
                     ('gw_LSTM', gw_LSTM)])

In [4]:
## Set hyperparameter grid
parameters = {'gw_LSTM__WINDOW_SIZE': [7, 60, 180, 365, 1000],
                 'gw_LSTM__NUM_FEATS': [12],
                 'gw_LSTM__LSTM_UNITS': [64],
                 'gw_LSTM__D_MAX_LAYERS': [8], 
                 'gw_LSTM__D_TOP_UNITS': [150], 
                 'gw_LSTM__D_MIN_UNITS': [3],
                 'gw_LSTM__D_UNIT_SCALE': [0.1],
                 'gw_LSTM__LEARNING_RATE': [0.0005], 
                 'gw_LSTM__EPOCHS': [30], 
                 'gw_LSTM__RANDOM_STATE': [90210],
                 'gw_LSTM__CHECKPOINT': [False],
                 'gw_LSTM__tmean': [well_tr_mean],
                 'gw_LSTM__tsd': [well_tr_std]}# 5 * 3^4 = 405
# I'm just accepting some data leakage here; the mean and standard deviation
# are taken over the whole training set which the time series split below
# is going to split into training and test sets
#
# If I were good, I would find a way to get mean and std for each of the 
# cross validation training sets and use that, but since this is about comparison
# between models, they'll all have the same data leakage, so I can justify
# my laziness in this case because I have no clue how to deal with the tscv

In [5]:
## Create the TimeSeriesSplit object
N_SPLITS = 3
tscv = TimeSeriesSplit(n_splits=N_SPLITS, test_size=365, gap=0)

## Create the GridSearchCV object
grid_search = GridSearchCV(pipe, parameters, cv=tscv, n_jobs=1)

## Fit the GridSearchCV object
grid_search.fit(np.array(X_train), y_train)

## Load the grid search results into a dataframe
results = pd.DataFrame(grid_search.cv_results_)
results.sort_values(by='rank_test_score', inplace=True)

## Create a timestamp
stamp = str(time.time())[:10]

## Save the results
with open('../scratch-work/LSTMgridsearchcv_results_APK309-'+stamp+'.pkl', 'wb') as f:
    pickle.dump(results, f)

2023-11-23 22:01:44.328261: I metal_plugin/src/device/metal_device.cc:1154] Metal device set to: Apple M2 Max
2023-11-23 22:01:44.328277: I metal_plugin/src/device/metal_device.cc:296] systemMemory: 64.00 GB
2023-11-23 22:01:44.328284: I metal_plugin/src/device/metal_device.cc:313] maxCacheSize: 24.00 GB
2023-11-23 22:01:44.328309: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:306] Could not identify NUMA node of platform GPU ID 0, defaulting to 0. Your kernel may not have been built with NUMA support.
2023-11-23 22:01:44.328332: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:272] Created TensorFlow device (/job:localhost/replica:0/task:0/device:GPU:0 with 0 MB memory) -> physical PluggableDevice (device: 0, name: METAL, pci bus id: <undefined>)


Epoch 1/30


2023-11-23 22:01:45.068315: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:117] Plugin optimizer for device_type GPU is enabled.
2023-11-23 22:01:45.111780: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:961] model_pruner failed: INVALID_ARGUMENT: Graph does not contain terminal node Adam/AssignAddVariableOp.


81/81 [==============================] - 1s 9ms/step - loss: 2012.3583 - root_mean_squared_error: 44.8593
Epoch 2/30
81/81 [==============================] - 1s 8ms/step - loss: 471.1415 - root_mean_squared_error: 21.7058
Epoch 3/30
81/81 [==============================] - 1s 8ms/step - loss: 1.9958 - root_mean_squared_error: 1.4127
Epoch 4/30
81/81 [==============================] - 1s 8ms/step - loss: 1.3174 - root_mean_squared_error: 1.1478
Epoch 5/30
81/81 [==============================] - 1s 8ms/step - loss: 0.9699 - root_mean_squared_error: 0.9848
Epoch 6/30
81/81 [==============================] - 1s 8ms/step - loss: 0.7845 - root_mean_squared_error: 0.8857
Epoch 7/30
81/81 [==============================] - 1s 8ms/step - loss: 0.6419 - root_mean_squared_error: 0.8012
Epoch 8/30
81/81 [==============================] - 1s 8ms/step - loss: 0.5351 - root_mean_squared_error: 0.7315
Epoch 9/30
81/81 [==============================] - 1s 8ms/step - loss: 0.4554 - root_mean_squared_e

/Users/marcos/miniconda3/envs/gw-project/lib/python3.10/site-packages/sklearn/model_selection/_validation.py:821: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/marcos/miniconda3/envs/gw-project/lib/python3.10/site-packages/sklearn/model_selection/_validation.py", line 810, in _score
    scores = scorer(estimator, X_test, y_test)
  File "/Users/marcos/miniconda3/envs/gw-project/lib/python3.10/site-packages/sklearn/metrics/_scorer.py", line 527, in __call__
    return estimator.score(*args, **kwargs)
  File "/Users/marcos/miniconda3/envs/gw-project/lib/python3.10/site-packages/sklearn/pipeline.py", line 760, in score
    return self.steps[-1][1].score(Xt, y, **score_params)
  File "/Users/marcos/MEGA/gitHub/erdos_groundwater/scratch-work/../gw_tools/gw_LSTM.py", line 157, in score
    score = np.mean((pred - y)**2)
ValueError: operands could not be broadcast together

...

89/89 [==============================] - 0s 4ms/step - loss: 0.7434 - root_mean_squared_error: 0.8622
Epoch 11/30
89/89 [==============================] - 0s 4ms/step - loss: 0.5285 - root_mean_squared_error: 0.7270
Epoch 12/30
89/89 [==============================] - 0s 4ms/step - loss: 0.4863 - root_mean_squared_error: 0.6973
Epoch 13/30
89/89 [==============================] - 0s 4ms/step - loss: 0.4554 - root_mean_squared_error: 0.6748
Epoch 14/30
89/89 [==============================] - 0s 4ms/step - loss: 0.3861 - root_mean_squared_error: 0.6214
Epoch 15/30
89/89 [==============================] - 0s 4ms/step - loss: 0.3309 - root_mean_squared_error: 0.5753
Epoch 16/30
89/89 [==============================] - 0s 4ms/step - loss: 0.3874 - root_mean_squared_error: 0.6224
Epoch 17/30
89/89 [==============================] - 0s 4ms/step - loss: 0.2995 - root_mean_squared_error: 0.5472
Epoch 18/30
89/89 [==============================] - 0s 4ms/step - loss: 0.3064 - root_mean_squared_

89/89 [==============================] - 0s 4ms/step - loss: 0.2730 - root_mean_squared_error: 0.5225
Epoch 20/30
89/89 [==============================] - 0s 4ms/step - loss: 0.2782 - root_mean_squared_error: 0.5275
Epoch 21/30
89/89 [==============================] - 0s 5ms/step - loss: 0.2282 - root_mean_squared_error: 0.4777
Epoch 22/30
89/89 [==============================] - 0s 5ms/step - loss: 0.2138 - root_mean_squared_error: 0.4624
Epoch 23/30
89/89 [==============================] - 0s 5ms/step - loss: 0.2270 - root_mean_squared_error: 0.4764
Epoch 24/30
89/89 [==============================] - 0s 5ms/step - loss: 0.1858 - root_mean_squared_error: 0.4310
Epoch 25/30
1/1 [==============================] - 0s 16ms/steploss: 0.2844 - root_mean_squared_error: 0.5333


89/89 [==============================] - 0s 5ms/step - loss: 0.2498 - root_mean_squared_error: 0.4998
Epoch 26/30
89/89 [==============================] - 0s 5ms/step - loss: 0.1947 - root_mean_squared_error: 0.4412
Epoch 27/30
89/89 [==============================] - 0s 5ms/step - loss: 0.1839 - root_mean_squared_error: 0.4289
Epoch 28/30
89/89 [==============================] - 0s 5ms/step - loss: 0.1595 - root_mean_squared_error: 0.3994
Epoch 29/30
89/89 [==============================] - 0s 5ms/step - loss: 0.1644 - root_mean_squared_error: 0.4054
Epoch 30/30
1/1 [==============================] - 0s 12ms/step


1/1 [==============================] - 0s 13ms/step


1/1 [==============================] - 0s 13ms/step
Epoch 1/30
101/101 [==============================] - 2s 5ms/step - loss: 3489.0664 - root_mean_squared_error: 59.0683
Epoch 2/30
101/101 [==============================] - 0s 4ms/step - loss: 8.5098 - root_mean_squared_error: 2.9172
Epoch 3/30
101/101 [==============================] - 1s 6ms/step - loss: 3.2986 - root_mean_squared_error: 1.8162
Epoch 4/30
101/101 [==============================] - 0s 4ms/step - loss: 1.9373 - root_mean_squared_error: 1.3919
Epoch 5/30
101/101 [==============================] - 0s 4ms/step - loss: 1.3181 - root_mean_squared_error: 1.1481
Epoch 6/30
101/101 [==============================] - 0s 4ms/step - loss: 1.1379 - root_mean_squared_error: 1.0667
Epoch 7/30
101/101 [==============================] - 0s 4ms/step - loss: 0.9300 - root_mean_squared_error: 0.9644
Epoch 8/30
1/1 [==============================] - 0s 12ms/step- loss: 0.8277 - root_mean_squared_error: 0.9098


In [6]:
pd.set_option('display.max_columns', None)
results.head(10)

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
0      23.133999      2.141728         8.437517        0.082639   
1      35.919803      3.759101         7.761286        0.072913   
2      46.432365      3.810881         5.089097        0.027553   
3      68.141901      7.794881         0.000473        0.000039   
4     118.337929     17.032571         0.000605        0.000032   

  param_gw_LSTM__CHECKPOINT param_gw_LSTM__D_MAX_LAYERS  \
0                     False                           8   
1                     False                           8   
2                     False                           8   
3                     False                           8   
4                     False                           8   

  param_gw_LSTM__D_MIN_UNITS param_gw_LSTM__D_TOP_UNITS  \
0                          3                        150   
1                          3                        150   
2                          3                        150   
3                          3                        150   
4                          3                        150   

  param_gw_LSTM__D_UNIT_SCALE param_gw_LSTM__EPOCHS  \
0                         0.1                    30   
1                         0.1                    30   
2                         0.1                    30   
3                         0.1                    30   
4                         0.1                    30   

  param_gw_LSTM__LEARNING_RATE param_gw_LSTM__LSTM_UNITS  \
0                       0.0005                        64   
1                       0.0005                        64   
2                       0.0005                        64   
3                       0.0005                        64   
4                       0.0005                        64   

  param_gw_LSTM__NUM_FEATS param_gw_LSTM__RANDOM_STATE  \
0                       12                       90210   
1                       12                       90210   
2                       12                       90210   
3                       12                       90210   
4                       12                       90210   

  param_gw_LSTM__WINDOW_SIZE param_gw_LSTM__tmean param_gw_LSTM__tsd  \
0                          7            47.494256           2.203425   
1                         60            47.494256           2.203425   
2                        180            47.494256           2.203425   
3                        365            47.494256           2.203425   
4                       1000            47.494256           2.203425   

                                              params  split0_test_score  \
0  {'gw_LSTM__CHECKPOINT': False, 'gw_LSTM__D_MAX...                NaN   
1  {'gw_LSTM__CHECKPOINT': False, 'gw_LSTM__D_MAX...                NaN   
2  {'gw_LSTM__CHECKPOINT': False, 'gw_LSTM__D_MAX...                NaN   
3  {'gw_LSTM__CHECKPOINT': False, 'gw_LSTM__D_MAX...                NaN   
4  {'gw_LSTM__CHECKPOINT': False, 'gw_LSTM__D_MAX...                NaN   

   split1_test_score  split2_test_score  mean_test_score  std_test_score  \
0                NaN                NaN              NaN             NaN   
1                NaN                NaN              NaN             NaN   
2                NaN                NaN              NaN             NaN   
3                NaN                NaN              NaN             NaN   
4                NaN                NaN              NaN             NaN   

   rank_test_score  
0                1  
1                1  
2                1  
3                1  
4                1